In [57]:
import ccxt

binance = ccxt.binance({
    "options": {"defaultType": "future"},
    "timeout": 30000,
    "enableRateLimit": False,
    })
binance.load_markets()



{'ETH/BTC': {'id': 'ETHBTC',
  'lowercaseId': 'ethbtc',
  'symbol': 'ETH/BTC',
  'base': 'ETH',
  'quote': 'BTC',
  'settle': None,
  'baseId': 'ETH',
  'quoteId': 'BTC',
  'settleId': None,
  'type': 'spot',
  'spot': True,
  'margin': True,
  'swap': False,
  'future': False,
  'option': False,
  'index': None,
  'active': True,
  'contract': False,
  'linear': None,
  'inverse': None,
  'subType': None,
  'taker': 0.001,
  'maker': 0.001,
  'contractSize': None,
  'expiry': None,
  'expiryDatetime': None,
  'strike': None,
  'optionType': None,
  'precision': {'amount': 4, 'price': 5, 'cost': None, 'base': 8, 'quote': 8},
  'limits': {'leverage': {'min': None, 'max': None},
   'amount': {'min': 0.0001, 'max': 100000.0},
   'price': {'min': 1e-05, 'max': 922327.0},
   'cost': {'min': 0.0001, 'max': 9000000.0},
   'market': {'min': 0.0, 'max': 2077.08681583}},
  'created': None,
  'info': {'symbol': 'ETHBTC',
   'status': 'TRADING',
   'baseAsset': 'ETH',
   'baseAssetPrecision': '8',

In [58]:
btc_ohlcv = binance.fetch_ohlcv("BTC/USDT", "1d")

In [59]:
import datetime
def timestamp_to_datetime(timestamp):
    datetimeobj = datetime.datetime.fromtimestamp(timestamp/1000)
    original_time_data = str(datetimeobj)
    entry_time_data = str(datetimeobj)[11:-3]
    exit_time_data = str(datetimeobj)[5:-3]
    return entry_time_data, exit_time_data, original_time_data

In [60]:
def TW(odd):
    return np.round(-np.log(0.99) / (np.log(1+0.01*odd) - np.log(0.99)), 4)

def shortest_distance(odd, winrate, n=100000):
    lins = np.linspace(0,10,n)
    y = TW(lins)
    least_distance = 1e+100
    for i in range(n):
        dx = lins[i] - odd
        dy = y[i] - winrate
        distance = np.sqrt(dx**2 + dy**2)
        if distance < least_distance:
            least_distance = distance
    if winrate > TW(odd):
        return np.round(least_distance, 10)
    else:
        return -1 * np.round(least_distance, 10)

def get_perfomance(trade_log):
    if len(trade_log) == 0:
        return None
    win = []
    lose = []
    risk_free = 0.038 / 365
    avg = np.mean(trade_log)
    std = np.std(trade_log)

    for i in range(len(trade_log)):
        if trade_log[i] > 0:
            win.append(trade_log[i])
        elif trade_log[i] < 0:
            lose.append(trade_log[i])

    avg_W_L_ratio = -1 * np.mean(win) / np.mean(lose)
    total_perform = shortest_distance(avg_W_L_ratio, len(win) / len(trade_log))
    # total_perform = Utils.shortest_distance(avg_W_L_ratio, len(win) / len(trade_log))
    size = (avg - risk_free) / (std * std)
    print('총거래 : ', len(trade_log))
    print('수익거래수 :', len(win))
    print('손실거래수 :', len(lose))
    print('평균거래 :',avg)
    print('평균수익거래 :', np.mean(win))
    print('평균손실거래 :', np.mean(lose))
    print('평균손익비 :', avg_W_L_ratio)
    win_rate = int(round(len(win) / len(trade_log),2) * 100)
    print('승률 :',win_rate , '%')
    print('포지션 사이징 :', size)
    if len(lose) > 0:
        print('최대 손실 :', min(lose))
    print(total_perform)
    print('')


In [62]:
ratio_vars = []

for i in range(3, len(btc_ohlcv)):
    d_2_ohlc = btc_ohlcv[i-2]
    d_1_ohlc = btc_ohlcv[i-1]
    d_day_ohlc = btc_ohlcv[i]

    d_2_low = d_2_ohlc[3]
    d_1_high = d_1_ohlc[2]

    d_day_high = d_day_ohlc[2]
    d_day_open = d_day_ohlc[1]

    ratio = round(d_1_high / d_2_low, 5) 
    ratio_vars.append(ratio)

    result = True if d_day_high / d_day_open > 1.01 else False

    date_var = timestamp_to_datetime(d_day_ohlc[0])[-1]

    print(f"date = {date_var}, ratio = {ratio}, result = {result}")

    # print(f"d_2_low : {d_2_low}")
    # print(f"d_1_high : {d_1_high}")
    # print(d_2_ohlc[0])



import numpy as np

print(sum(ratio_vars) / len(ratio_vars))
print(np.median(ratio_vars))





date = 2023-05-28 09:00:00, ratio = 1.02189, result = True
date = 2023-05-29 09:00:00, ratio = 1.06499, result = True
date = 2023-05-30 09:00:00, ratio = 1.06341, result = True
date = 2023-05-31 09:00:00, ratio = 1.01909, result = False
date = 2023-06-01 09:00:00, ratio = 1.01072, result = False
date = 2023-06-02 09:00:00, ratio = 1.01946, result = True
date = 2023-06-03 09:00:00, ratio = 1.02594, result = False
date = 2023-06-04 09:00:00, ratio = 1.03258, result = True
date = 2023-06-05 09:00:00, ratio = 1.02082, result = False
date = 2023-06-06 09:00:00, ratio = 1.00704, result = True
date = 2023-06-07 09:00:00, ratio = 1.07879, result = False
date = 2023-06-08 09:00:00, ratio = 1.08186, result = True
date = 2023-06-09 09:00:00, ratio = 1.02639, result = True
date = 2023-06-10 09:00:00, ratio = 1.02213, result = False
date = 2023-06-11 09:00:00, ratio = 1.01102, result = True
date = 2023-06-12 09:00:00, ratio = 1.03553, result = False
date = 2023-06-13 09:00:00, ratio = 1.01859, resu

In [63]:
def TW(odd):
    return np.round(-np.log(0.99) / (np.log(1+0.01*odd) - np.log(0.99)), 4)

def shortest_distance(odd, winrate, n=100000):
    lins = np.linspace(0,10,n)
    y = TW(lins)
    least_distance = 1e+100
    for i in range(n):
        dx = lins[i] - odd
        dy = y[i] - winrate
        distance = np.sqrt(dx**2 + dy**2)
        if distance < least_distance:
            least_distance = distance
    if winrate > TW(odd):
        return np.round(least_distance, 10)
    else:
        return -1 * np.round(least_distance, 10)

def get_perfomance(trade_log):
    if len(trade_log) == 0:
        return None
    win = []
    lose = []
    risk_free = 0.038 / 365
    avg = np.mean(trade_log)
    std = np.std(trade_log)

    for i in range(len(trade_log)):
        if trade_log[i] > 0:
            win.append(trade_log[i])
        elif trade_log[i] < 0:
            lose.append(trade_log[i])

    avg_W_L_ratio = -1 * np.mean(win) / np.mean(lose)
    total_perform = shortest_distance(avg_W_L_ratio, len(win) / len(trade_log))
    # total_perform = Utils.shortest_distance(avg_W_L_ratio, len(win) / len(trade_log))
    size = (avg - risk_free) / (std * std)
    print('총거래 : ', len(trade_log))
    print('수익거래수 :', len(win))
    print('손실거래수 :', len(lose))
    print('평균거래 :',avg)
    print('평균수익거래 :', np.mean(win))
    print('평균손실거래 :', np.mean(lose))
    print('평균손익비 :', avg_W_L_ratio)
    win_rate = int(round(len(win) / len(trade_log),2) * 100)
    print('승률 :',win_rate , '%')
    print('포지션 사이징 :', size)
    if len(lose) > 0:
        print('최대 손실 :', min(lose))
    print(total_perform)
    print('')


In [72]:
total_earning = []

for i in range(3, len(btc_ohlcv)):
    d_2_ohlc = btc_ohlcv[i-2]
    d_1_ohlc = btc_ohlcv[i-1]
    d_day_ohlc = btc_ohlcv[i]

    d_2_low = d_2_ohlc[3]
    d_1_high = d_1_ohlc[2]

    d_day_high = d_day_ohlc[2]
    d_day_open = d_day_ohlc[1]
    d_day_close= d_day_ohlc[4]
    

    ratio = round(d_1_high / d_2_low, 5) 
    
    

    earning = 0
    if ratio > 1.03:
        earning = 1.011 if d_day_high / d_day_open > 1.011 else d_day_close / d_day_open
        earning = round(((earning * 0.9988 - 1) * 100), 3)
        # earning -= 1
        total_earning.append(earning)

    date_var = timestamp_to_datetime(d_day_ohlc[0])[-1]

    print(f"date = {date_var}, ratio = {ratio}, earning = {earning}")

    # print(f"d_2_low : {d_2_low}")
    # print(f"d_1_high : {d_1_high}")
    # print(d_2_ohlc[0])


print(sum(total_earning))
print(len(total_earning))


get_perfomance(total_earning)

.

date = 2023-05-28 09:00:00, ratio = 1.02189, earning = 0
date = 2023-05-29 09:00:00, ratio = 1.06499, earning = 0.979
date = 2023-05-30 09:00:00, ratio = 1.06341, earning = 0.979
date = 2023-05-31 09:00:00, ratio = 1.01909, earning = 0
date = 2023-06-01 09:00:00, ratio = 1.01072, earning = 0
date = 2023-06-02 09:00:00, ratio = 1.01946, earning = 0
date = 2023-06-03 09:00:00, ratio = 1.02594, earning = 0
date = 2023-06-04 09:00:00, ratio = 1.03258, earning = 0.979
date = 2023-06-05 09:00:00, ratio = 1.02082, earning = 0
date = 2023-06-06 09:00:00, ratio = 1.00704, earning = 0
date = 2023-06-07 09:00:00, ratio = 1.07879, earning = -3.406
date = 2023-06-08 09:00:00, ratio = 1.08186, earning = 0.979
date = 2023-06-09 09:00:00, ratio = 1.02639, earning = 0
date = 2023-06-10 09:00:00, ratio = 1.02213, earning = 0
date = 2023-06-11 09:00:00, ratio = 1.01102, earning = 0
date = 2023-06-12 09:00:00, ratio = 1.03553, earning = -0.179
date = 2023-06-13 09:00:00, ratio = 1.01859, earning = 0
date 